# Entrainement inspiré par mosaicml/mpt-7b-instruct

## Installation des librairies manquantes

In [1]:
#! pip install --upgrade git+https://github.com/huggingface/transformers

In [2]:
! pip uninstall transformers -y
! pip install transformers

Found existing installation: transformers 4.33.0
Uninstalling transformers-4.33.0:
  Successfully uninstalled transformers-4.33.0
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.9/7.9 MB 53.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 80.1 MB/s eta 0:00:00
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.13.3
    Uninstalling tokenizers-0.13.3:
      Successfully uninstalled tokenizers-0.13.3


In [3]:
import transformers
print(transformers.__version__)

4.35.0


In [4]:
! pip install bitsandbytes
! pip install einops
! pip install peft
! pip install trl

# Bug selon la version de datasets, besoin d'installer une version plus récente que celle de l'environnement pré-installé :
! pip uninstall datasets -y
! pip install datasets==2.13.1

import datasets
datasets.__version__

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.6/92.6 MB 14.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.9/134.9 kB 4.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.0/124.0 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.9/99.9 kB 9.6 MB/s eta 0:00:00
Found existing installation: datasets 2.1.0
Uninstalling datasets-2.1.0:
  Successfully uninstalled datasets-2.1.0
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 486.2/486.2 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 12.1 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of multiprocess to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 14.1 MB/s eta 0:00:00
  Attempting uninstall: dill
    Found existing installation: dill 0.3.7
    Uninstalling 

'2.13.1'

## Import des librairies

In [5]:
import einops
import torch
from datasets import load_dataset
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, TrainingArguments
from peft import LoraConfig
from trl import SFTTrainer

/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.5
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


## Téléchargement du dataset pour le fine tuning

In [6]:

dataset_name = "Laurent1/MedQuad-MedicalQnADataset_128tokens_max" 
# On fine tune les 5000 premieres questions sinon c'est un peu long...
dataset = load_dataset(dataset_name, split='train[:5120]')
dataset

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Dataset csv downloaded and prepared to /root/.cache/huggingface/datasets/Laurent1___csv/Laurent1--MedQuad-MedicalQnADataset_128tokens_max-2fc5fd9a3c22611f/0.0.0/eea64c71ca8b46dd3f537ed218fc9bf495d5707789152eb2764f5c78fa66d59d. Subsequent calls will reuse this data.


Dataset({
    features: ['text'],
    num_rows: 5120
})

## Téléchargement du model pre-entrainé et de son tokenizer

In [7]:
# BitsAndBytes permet le fine tuning avec "quantification" pour réduire l'impact mémoire et les calculs
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.float16,
)

model = AutoModelForCausalLM.from_pretrained(
        "mistralai/Mistral-7B-Instruct-v0.1",
        device_map="auto",
        torch_dtype=torch.float16, #torch.bfloat16,
        trust_remote_code=True
            )

tokenizer = AutoTokenizer.from_pretrained("mistralai/Mistral-7B-Instruct-v0.1")
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right" 

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [8]:
tokenizer = AutoTokenizer.from_pretrained("mistralai/Mistral-7B-Instruct-v0.1")
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right" 

## Configuration du peft LoRa

In [9]:
lora_alpha = 16
lora_dropout = 0.1
lora_r = 32

peft_config = LoraConfig(
    lora_alpha=lora_alpha,
    lora_dropout=lora_dropout,
    r=lora_r,
    bias="none",
    task_type="CAUSAL_LM",
    target_modules=[
        "Wqkv",
        "out_proj",
        "up_proj",
        "down_proj",
    ]
)

## Préparation de l'entraineur (Supervised Fine-tuning Trainer)

Utilisation de [`SFTTrainer` de la librairie TRL](https://huggingface.co/docs/trl/main/en/sft_trainer) qui est un wrapper de Trainer facilite le fine tuning avec LoRa

In [10]:
output_dir = "/kaggle/working/"
per_device_train_batch_size = 1
gradient_accumulation_steps = 16
optim = "paged_adamw_32bit"
save_steps = 64
logging_steps = 64
learning_rate = 1e-4
max_grad_norm = 0.3
max_steps = 1600
warmup_ratio = 0.03
lr_scheduler_type = "linear"

training_arguments = TrainingArguments(
    output_dir=output_dir,
    per_device_train_batch_size=per_device_train_batch_size,
    gradient_accumulation_steps=gradient_accumulation_steps,
    optim=optim,
    #save_steps=save_steps,
    logging_steps=logging_steps,
    
    #num_train_epochs=5,# *************
    #logging_strategy='epoch',# *************
    
    save_strategy= 'no', #''epoch',# *************
    
    learning_rate=learning_rate,
    fp16=True,
    max_grad_norm=max_grad_norm,
    max_steps=max_steps,
    warmup_ratio=warmup_ratio,
    group_by_length=True,
    lr_scheduler_type=lr_scheduler_type,
    report_to = 'none',
    save_total_limit = 1
)

In [11]:
trainer = SFTTrainer(
    model=model,
    train_dataset=dataset,
    peft_config=peft_config,
    dataset_text_field="text",
    max_seq_length= 512,
    tokenizer=tokenizer,
    args=training_arguments,
)

Map:   0%|          | 0/5120 [00:00<?, ? examples/s]

## Entrainement du model

In [12]:
trainer.train()

You're using a LlamaTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=1600, training_loss=0.6009962081909179, metrics={'train_runtime': 6674.4421, 'train_samples_per_second': 3.836, 'train_steps_per_second': 0.24, 'total_flos': 1.2489013664022528e+17, 'train_loss': 0.6009962081909179, 'epoch': 5.0})

In [13]:
trainer.save_model('/kaggle/working/')